# Infer Pooled PK Model Parameters from Individuals in Lung Cancer Treatment Group with Low, Medium and High Erlotinib Dose

## Preclinical data

In [3]:
import erlotinib as erlo
import pandas as pd

# Get data
data_low = erlo.DataLibrary().lung_cancer_low_erlotinib_dose_group()
data_medium = erlo.DataLibrary().lung_cancer_medium_erlotinib_dose_group()
data_high = erlo.DataLibrary().lung_cancer_high_erlotinib_dose_group()
data = pd.concat([data_low, data_medium, data_high])

# Create scatter plot
# Low dose
fig = erlo.plots.PKTimeSeriesPlot()
fig.add_data(data_low, biomarker='Plasma concentration')
fig.set_axis_labels(
    time_label=r'$\text{Time in day}$', 
    biom_label=r'$\text{Plasma concentration in ng/mL}$', 
    dose_label=r'$\text{Dose in mg}$')
fig.show()

# Medium dose
fig = erlo.plots.PKTimeSeriesPlot()
fig.add_data(data_medium, biomarker='Plasma concentration')
fig.set_axis_labels(
    time_label=r'$\text{Time in day}$', biom_label=r'$\text{Plasma concentration in ng/mL}$', 
    dose_label=r'$\text{Dose in mg}$')
fig.show()

# High dose
fig = erlo.plots.PKTimeSeriesPlot()
fig.add_data(data_high, biomarker='Plasma concentration')
fig.set_axis_labels(
    time_label=r'$\text{Time in day}$', biom_label=r'$\text{Plasma concentration in ng/mL}$', 
    dose_label=r'$\text{Dose in mg}$')
fig.show()

In [11]:
mask = data_low['ID'] == 38
temp = data_low[mask]
mask = temp['Time'] == 11
temp[mask]

ID  Time Time unit             Biomarker  Measurement Biomarker unit  \
18   38  11.0         d         Tumour volume     0.212544           cm^3   
19   38  11.0         d         Tumour volume          NaN           cm^3   
205  38  11.0         d           Body weight    26.800000              g   
206  38  11.0         d           Body weight          NaN              g   
392  38  11.0         d  Plasma concentration          NaN          ng/mL   
393  38  11.0         d  Plasma concentration          NaN          ng/mL   
570  38  11.0         d                   NaN          NaN            NaN   
571  38  11.0         d                   NaN          NaN            NaN   

        Dose Dose unit  Duration  
18       NaN       NaN       NaN  
19       NaN       NaN       NaN  
205      NaN       NaN       NaN  
206      NaN       NaN       NaN  
392      NaN       NaN       NaN  
393      NaN       NaN       NaN  
570  0.16875        mg       NaN  
571  0.16875        mg       NaN

**Figure 1:** Visualisation of the measured erlotinib pharmacokinetic data in 8 mice with patient-derived lung cancer implants. The bottom subplot shows the measured plasma concentration time series. The top subplot displays the administered oral doses of erlotinib for each mouse.

## Build Population PK model

In [5]:
import erlotinib as erlo

# Define mechanistic model
path = erlo.ModelLibrary().one_compartment_pk_model()
mechanistic_model = erlo.PharmacokineticModel(path)
mechanistic_model.set_administration(compartment='central', direct=False)
mechanistic_model.set_parameter_names(names={
    'central.drug_amount': 'Initial plasma drug amount in mg',
    'dose.drug_amount': 'Initial dose comp. drug amount in mg',
    'central.size': 'Volume of distribution in L',
    'dose.absorption_rate': 'Absorption rate in 1/d',
    'myokit.elimination_rate': 'Elimination rate in 1/d'})

# Define error model
error_model = erlo.ConstantAndMultiplicativeGaussianErrorModel()

# Define population model
population_models = [
    erlo.PooledModel(),   # Volume of distribution
    erlo.PooledModel(),   # Absorption rate
    erlo.PooledModel(),   # Elimination rate
    erlo.PooledModel(),   # Plasma concentration sigma base
    erlo.PooledModel(),]  # Plasma concentration sigma rel.

# Build model
problem = erlo.ProblemModellingController(
    mechanistic_model, error_model)
problem.fix_parameters(name_value_dict={
    'Initial plasma drug amount in mg': 0,
    'Initial dose comp. drug amount in mg': 0})

## Prior predictive checks

In [8]:
import numpy as np
import pints

# Define prior distribution
log_priors = [
    pints.HalfCauchyLogPrior(location=0, scale=1),     # Volume of distribution
    pints.HalfCauchyLogPrior(location=1, scale=2),     # Absorption rate
    pints.HalfCauchyLogPrior(location=0, scale=0.1),   # Elimination rate
    pints.HalfCauchyLogPrior(location=0, scale=1),     # Sigma base
    pints.HalfCauchyLogPrior(location=0, scale=0.1)]   # Sigma rel.
log_prior = pints.ComposedLogPrior(*log_priors)

# Define prior predictive model and sample 1000 virtual patients
predictive_model = problem.get_predictive_model(exclude_pop_model=True)
model = erlo.PriorPredictiveModel(predictive_model, log_prior)
seed = 42
n_samples = 1000
times = np.linspace(start=0, stop=30, num=100)

# Visualise prior predictive model
# Low dose 
model.set_dosing_regimen(0.16, start=3, period=1, num=14)
samples = model.sample(times, n_samples, seed)
fig = erlo.plots.PDPredictivePlot()
fig.add_prediction(data=samples, bulk_probs=[0.3, 0.6, 0.9])
fig.set_axis_labels(xlabel=r'$\text{Time in day}$', ylabel=r'$\text{Plasma conc. in ng/mL}$')
fig.show()

# Medium dose 
model.set_dosing_regimen(0.65, start=3, period=1, num=14)
samples = model.sample(times, n_samples, seed)
fig = erlo.plots.PDPredictivePlot()
fig.add_prediction(data=samples, bulk_probs=[0.3, 0.6, 0.9])
fig.set_axis_labels(xlabel=r'$\text{Time in day}$', ylabel=r'$\text{Plasma conc. in ng/mL}$')
fig.show()

# High dose 
model.set_dosing_regimen(2.5, start=3, period=1, num=14)
samples = model.sample(times, n_samples, seed)
fig = erlo.plots.PDPredictivePlot()
fig.add_prediction(data=samples, bulk_probs=[0.3, 0.6, 0.9])
fig.set_axis_labels(xlabel=r'$\text{Time in day}$', ylabel=r'$\text{Plasma conc. in ng/mL}$')
fig.show()

**Figure 2:** Prior predictive model of tumour volume measurement over time. The shaded areas estimate the 0.3, 0.6 and 0.9 bulk probability of the prior predictive distribution by sampling 1000 virtual "measurements" at each of the time points.

## Find MAP estimates for model parameters

In [9]:
# Create posterior
problem.set_data(data, output_biomarker_dict={'central.drug_concentration': 'Plasma concentration'})
problem.set_log_prior(log_priors)
log_posterior = problem.get_log_posteriors()

# Find maximum a posteriori probability estimates (MAP)
opt = erlo.OptimisationController(log_posterior)
opt.set_transform(transform=pints.LogTransformation(n_parameters=5))
map_estimates = opt.run(show_run_progress_bar=True)

SimultaneousProtocolEventError: Two events cannot (re-)start at the same time: Error at time t=11.0.

### Visualise optimisation results

In [3]:
fig = erlo.plots.ParameterEstimatePlot()
fig.add_data(map_estimates)

fig.show()

**Figure 2:** Maximum a posteriori (MAP) estimates of the model parameters. The y axis displays the estimated parameter value, and the x axis the corresponding individual.

## Find posterior probability distribution

In [4]:
# Set up sampling controller
sampler = erlo.SamplingController(log_posteriors)
sampler.set_initial_parameters(data=map_estimates)
sampler.set_transform(transform=pints.LogTransformation(n_parameters=5))

# Run sampling
posterior_samples = sampler.run(n_iterations=4000, show_progress_bar=True)

### Visualise marginal posteriors

In [5]:
fig = erlo.plots.MarginalPosteriorPlot()
fig.add_data(data=posterior_samples, warm_up_iter=2000)

fig.show()

**Figure 3:** Marginal posterior distributions of model parameters. The y axis displays the sampled parameter value, and the x axis the binned number of samples for each individual.